In [1]:
import pandas as pd
import xml.etree.ElementTree as ET
import glob, os
import numpy as np
from comet_ml import Experiment, Optimizer
import pickle
import logging
import sys
from sklearn.utils import class_weight

In [2]:
os.environ["CUDA_DEVICE_ORDER"] = "PCI_BUS_ID"
os.environ["CUDA_VISIBLE_DEVICES"] = "0"
os.environ['TF_KERAS'] = '1'

# only reserve 1 GPU

In [3]:
import tensorflow as tf
tf.version

<module 'tensorflow._api.v2.version' from '/home/anasab/tftf3.6/local/lib/python3.6/site-packages/tensorflow/_api/v2/version/__init__.py'>

In [4]:
from tensorflow.keras.preprocessing import sequence
from tensorflow.keras.models import Sequential, Model, load_model
from tensorflow.keras.layers import Dense, Dropout, Embedding, LSTM, Lambda, BatchNormalization, TimeDistributed, \
     Bidirectional, Input, concatenate, Flatten, RepeatVector, Activation, Multiply, Permute#, CuDNNLSTM
from tensorflow.keras import regularizers
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras import callbacks, optimizers
from tensorflow.keras import backend as K
from tensorflow.keras.utils import plot_model, Sequence

from nltk.tokenize import RegexpTokenizer
from nltk.corpus import stopwords

import tensorflow as tf

In [5]:
import tensorflow as tf
tf.test.is_gpu_available()

Instructions for updating:
Use `tf.config.list_physical_devices('GPU')` instead.


True

In [6]:
my_seed = 1234
# tf.set_random_seed(my_seed)

In [7]:
logger = logging.getLogger('training')
logger.addHandler(logging.StreamHandler(sys.stdout))
logger.setLevel(logging.DEBUG)

# Read data

In [8]:
def read_subject_writings(subject_file):
    writings = []
    with open(subject_file) as sf:
        contents = sf.read()
        root = ET.fromstring(contents)
        try:
            subject = root.findall('ID')[0].text.strip()
        except Exception:
            print('Cannot extract ID', contents[:500], '\n-------\n')        
        for w in root.iter('WRITING'):
            subject_writings = {'subject': subject}
            for title in w.findall('TITLE'):
                subject_writings['title'] = title.text
            for text in w.findall('TEXT'):
                subject_writings['text'] = text.text
            for date in w.findall('DATE'):
                subject_writings['date'] = date.text
            writings.append(subject_writings)
    return writings

In [9]:
# root_dir = '/home/anasab/' 
root_dir = '/home/anasab/'

In [10]:
datadir_T2 = root_dir + '/eRisk/data/eRisk2020_T2/eRisk2020_T2_TRAINING_DATA/'
labels_file_T2 = root_dir + '/eRisk/data/eRisk2020_T2/eRisk2020_T2_TRAINING_DATA/Depression Questionnaires_anon.txt'
nr_questions = 21

In [11]:
def read_texts(datadir_T2,
                labels_file_T2):
    writings = []
    writings_df = pd.DataFrame()
    labels_df = pd.DataFrame()

        
    for subject_file in os.listdir(datadir_T2):
        if not subject_file.startswith('subject'):
            continue
        writings.extend(read_subject_writings(os.path.join(datadir_T2, subject_file)))
    writings_df = pd.DataFrame(writings)
    
    labels_df = pd.read_csv(os.path.join(labels_file_T2), 
                                 delimiter='\s+', names=['subject'] + ['label%i' % i for i in range(nr_questions)])

    labels_df = labels_df.set_index('subject')
    
    writings_df = writings_df.join(labels_df, on='subject')
    
    return writings_df, labels_df

In [12]:
# writings_df, labels_df = read_texts(datadir_T2, labels_file_T2)
writings_df = pickle.load(open('writings_df_T2_liwc.pkl', 'rb'))

In [13]:
writings_df.groupby('subject').count()

title  text  date  label0  label1  label2  label3  label4  \
subject                                                                  
subject1272    120   120   120     120     120     120     120     120   
subject2341    129   129   129     129     129     129     129     129   
subject2432    332   332   332     332     332     332     332     332   
subject2827    663   663   663     663     663     663     663     663   
subject2903    313   313   313     313     313     313     313     313   
subject2961    180   180   180     180     180     180     180     180   
subject3707   1022  1022  1022    1022    1022    1022    1022    1022   
subject3993   1510  1510  1510    1510    1510    1510    1510    1510   
subject4058   1028  1028  1028    1028    1028    1028    1028    1028   
subject436      29    29    29      29      29      29      29      29   
subject5791    303   303   303     303     303     303     303     303   
subject5897     82    82    82      82      82      82      82      82   
subject6619    514   514   514     514     514     514     514     514   
subject6635   1054  1054  1054    1054    1054    1054    1054    1054   
subject6900    313   313   313     313     313     313     313     313   
subject7039    561   561   561     561     561     561     561     561   
subject9218    323   323   323     323     323     323     323     323   
subject9454    180   180   180     180     180     180     180     180   
subject9694   1001  1001  1001    1001    1001    1001    1001    1001   
subject9798   1284  1284  1284    1284    1284    1284    1284    1284   

             label5  label6  ...  feel  excl  future  nonfl  ppron  shehe  \
subject                      ...                                            
subject1272     120     120  ...   120   120     120    120    120    120   
subject2341     129     129  ...   129   129     129    129    129    129   
subject2432     332     332  ...   332   332     332    332    332    332   
subject2827     663     663  ...   659   659     659    659    659    659   
subject2903     313     313  ...   313   313     313    313    313    313   
subject2961     180     180  ...   180   180     180    180    180    180   
subject3707    1022    1022  ...  1022  1022    1022   1022   1022   1022   
subject3993    1510    1510  ...  1509  1509    1509   1509   1509   1509   
subject4058    1028    1028  ...  1028  1028    1028   1028   1028   1028   
subject436       29      29  ...    29    29      29     29     29     29   
subject5791     303     303  ...   303   303     303    303    303    303   
subject5897      82      82  ...    82    82      82     82     82     82   
subject6619     514     514  ...   514   514     514    514    514    514   
subject6635    1054    1054  ...  1054  1054    1054   1054   1054   1054   
subject6900     313     313  ...   313   313     313    313    313    313   
subject7039     561     561  ...   560   560     560    560    560    560   
subject9218     323     323  ...   323   323     323    323    323    323   
subject9454     180     180  ...   180   180     180    180    180    180   
subject9694    1001    1001  ...   995   995     995    995    995    995   
subject9798    1284    1284  ...  1281  1281    1281   1281   1281   1281   

                i    we   you  they  
subject                              
subject1272   120   120   120   120  
subject2341   129   129   129   129  
subject2432   332   332   332   332  
subject2827   659   659   659   659  
subject2903   313   313   313   313  
subject2961   180   180   180   180  
subject3707  1022  1022  1022  1022  
subject3993  1509  1509  1509  1509  
subject4058  1028  1028  1028  1028  
subject436     29    29    29    29  
subject5791   303   303   303   303  
subject5897    82    82    82    82  
subject6619   514   514   514   514  
subject6635  1054  1054  1054  1054  
subject6900   313   313   313   313  
subject7039   560   560   560   560  
subje

In [14]:
writings_df

subject                                              title  \
0      subject5791                                                      
1      subject5791            The search button gives me a 404 error    
2      subject5791                                                      
3      subject5791                                                      
4      subject5791                                                      
...            ...                                                ...   
10936  subject3993   Alternative Currency Being Considered in Penn...   
10937  subject3993   Asus' new keyboard. Oh wait... thats not a ke...   
10938  subject3993   Homeland Security USA - tripe to entertain mo...   
10939  subject3993   10 dead as Israeli missile hits near U.N. sch...   
10940  subject3993        iPhone Apps: Helping People Get Rich Quick    

                                                    text  \
0                                  Great, thanks a ton!    
1       Just downloaded GBA4ios 2.1 and when I go to ...   
2                                      Remindme! 1 week    
3                                         Me too please    
4       Any chance you can pm me what this spoiler is...   
...                                                  ...   
10936                                                      
10937                                                      
10938                                                      
10939                                                      
10940                                                      

                        date  label0  label1  label2  label3  label4  label5  \
0       2018-10-30 17:35:30        1       0       1       1       0       0   
1       2018-10-30 17:19:41        1       0       1       1       0       0   
2       2018-10-30 14:33:49        1       0       1       1       0       0   
3       2018-10-19 18:06:38        1       0       1       1       0       0   
4       2018-10-19 18:04:14        1       0       1       1       0       0   
...                      ...     ...     ...     ...     ...     ...     ...   
10936   2009-01-07 18:41:30        0       0       0       0       0       0   
10937   2009-01-07 17:13:53        0       0       0       0       0       0   
10938   2009-01-07 07:09:19        0       0       0       0       0       0   
10939   2009-01-06 17:15:24        0       0       0       0       0       0   
10940   2009-01-06 07:25:07        0       0       0       0       0       0   

       ...  feel      excl    future  nonfl     ppron  shehe         i   we  \
0      ...   0.0  0.000000  0.000000    0.0  0.000000    0.0  0.000000  0.0   
1      ...   0.0  0.074468  0.074468    0.0  0.063830    0.0  0.063830  0.0   
2      ...   0.0  0.000000  0.000000    0.0  0.000000    0.0  0.000000  0.0   
3      ...   0.0  0.000000  0.000000    0.0  0.333333    0.0  0.333333  0.0   
4      ...   0.0  0.027778  0.111111    0.0  0.138889    0.0  0.111111  0.0   
...    ...   ...       ...       ...    ...       ...    ...       ...  ...   
10936  ...   0.0  0.000000  0.000000    0.0  0.000000    0.0  0.000000  0.0   
10937  ...   0.0  0.076923  0.076923    0.0  0.000000    0.0  0.000000  0.0   
10938  ...   0.0  0.000000  0.000000    0.0  0.000000    0.0  0.000000  0.0   
10939  ...   0.0  0.000000  0.000000    0.0  0.000000    0.0  0.000000  0.0   
10940  ...   0.0  0.000000  0.000000    0.0  0.000000    0.0  0.000000  0.0   

            you  they  
0      0.000000   0.0  
1      0.000000   0.0  
2      0.000000   0.0  
3      0.000000   0.0  
4      0.027778   0.0  
...         ...   ...  
10936  0.000000   0.0  
10937  0.000000   0.0  
10938  0.000000   0.0  
10939  0.000000   0.0  
10940  0.000000   0.0  

[10941 rows x 104 columns]

## Preprocess text

In [15]:
tokenizer = RegexpTokenizer(r'\w+')

def tokenize(t):
    return tokenizer.tokenize(t.lower())

In [16]:
def tokenize_fields(writings_df):
    writings_df['tokenized_title'] = writings_df['title'].apply(lambda t: tokenize(t) 
                                                                if type(t)==str and t else None)
    writings_df['title_len'] = writings_df['tokenized_title'].apply(lambda t: len(t) 
                                                                    if type(t)==list and t else None)
    writings_df['tokenized_text'] = writings_df['text'].apply(lambda t: tokenize(t) 
                                                              if type(t)==str and t else None)
    writings_df['text_len'] = writings_df['tokenized_text'].apply(lambda t: len(t) 
                                                                  if type(t)==list and t else None)
    return writings_df

In [17]:
writings_df = tokenize_fields(writings_df)

In [18]:
writings_df.text_len.describe()

count    10409.000000
mean        50.365069
std         84.811676
min          1.000000
25%          9.000000
50%         24.000000
75%         54.000000
max       1567.000000
Name: text_len, dtype: float64

In [19]:
writings_df.title_len.describe()

count    1119.000000
mean       11.246649
std         6.979392
min         1.000000
25%         6.000000
50%        10.000000
75%        15.000000
max        51.000000
Name: title_len, dtype: float64

In [20]:
writings_df.groupby('subject').count().title.describe()

count      20.000000
mean      547.050000
std       446.144828
min        29.000000
25%       180.000000
50%       327.500000
75%      1006.250000
max      1510.000000
Name: title, dtype: float64

In [21]:
writings_df.groupby('subject').count().text.describe()

count      20.000000
mean      547.050000
std       446.144828
min        29.000000
25%       180.000000
50%       327.500000
75%      1006.250000
max      1510.000000
Name: text, dtype: float64

# RoBERTa & co

In [22]:
from simpletransformers.classification import MultiLabelClassificationModel


In [23]:
seq_len = 300

In [24]:
# Aggregate by users
writings_df = writings_df.fillna(value={'text': '', 'title':''})
column_functions = {'text': lambda t: " ".join(t), 
                                        'title': lambda t: " ".join(t),
                                        'text_len': 'sum',
                                        'title_len': 'sum'}
column_functions.update({'label%i'%i: 'min' for i in range(21)})
writings_per_user_df = writings_df.groupby('subject').aggregate(column_functions)
#                                          'subset': 'min'})
# writings_per_user_df = writings_per_user_df.fillna("")
writings_per_user_df['text'] = writings_per_user_df['text'] + " " +  writings_per_user_df['title']
writings_per_user_df['text_len'] = writings_per_user_df['text_len'] + writings_per_user_df['title_len']

In [25]:
writings_per_user_df.text_len.describe()

count        20.000000
mean      26841.750000
std       33383.871337
min        1168.000000
25%        7118.750000
50%       15522.500000
75%       27742.000000
max      110673.000000
Name: text_len, dtype: float64

In [26]:
def reverse_text(text):
    return " ".join(text.split()[::-1])
def truncate_text_beginning(text, seq_len=seq_len, epsilon=20):
    truncated_tokenized = text.split()[-seq_len-epsilon:]
    return " ".join(truncated_tokenized)
# writings_per_user_df['text'] = writings_per_user_df['text'].apply(truncate_text_beginning)

In [27]:
def get_subjects_split(writings_df, train_prop=0.8, test_slice=2, nr_slices=5, valid_prop=0):
    if 'subset' in writings_df.columns:
        training_subjects = list(set(writings_df[writings_df['subset']=='train'].subject))
        test_subjects = list(set(writings_df[writings_df['subset']=='test'].subject))
    else:
        all_subjects = sorted(list(set(writings_df.subject)))
        training_subjects_size = int(len(all_subjects) * train_prop)
        test_subjects_size = len(all_subjects) - training_subjects_size
        # Cross-validation, with fixed slice as input
        test_prop = 1-train_prop
        test_slice = min(test_slice, nr_slices)
        logger.debug("start index: %f, from %f\n" % (
            len(all_subjects)*(1/nr_slices)*test_slice, test_prop*test_slice))
        start_slice = int(len(all_subjects)*(1/nr_slices)*test_slice)
        test_subjects = all_subjects[start_slice: start_slice+test_subjects_size]
        training_subjects = [s for s in all_subjects if s not in test_subjects]
    training_subjects = sorted(training_subjects) # ensuring reproducibility
    valid_subjects_size = int(len(training_subjects) * valid_prop)
    valid_subjects = training_subjects[:valid_subjects_size]
    training_subjects = training_subjects[valid_subjects_size:]
    logger.debug("%d training users, %d validation users, %d test users." % (
        len(training_subjects), 
          len(valid_subjects),
          len(test_subjects)))
    subjects_split = {'train': training_subjects, 
                      'valid': valid_subjects, 
                      'test': test_subjects}
    return subjects_split

subjects_split = get_subjects_split(writings_df, nr_slices=5, test_slice=4)

start index: 16.000000, from 0.800000

16 training users, 0 validation users, 4 test users.


In [28]:
train_df = writings_per_user_df[writings_per_user_df.index.isin(subjects_split['train'])]#[['text', 'labels']]
test_df = writings_per_user_df[writings_per_user_df.index.isin(subjects_split['test'])]#[['text', 'labels']]

In [29]:
train_df.head()

text  \
subject                                                          
subject1272   Just waking up every morning and talking to m...   
subject2341   If you need to talk to someone, it's not a ba...   
subject2432   *kid   A dataminer said that the octoling gir...   
subject2827   Im so sorry youve had a negative experience. ...   
subject2903   That was not at all how it was, but not gonna...   

                                                         title  text_len  \
subject                                                                    
subject1272                                                ...    1168.0   
subject2341                                                ...    6911.0   
subject2432                                                ...    7188.0   
subject2827           Opinions on high school anxiety      ...   17140.0   
subject2903                                                ...   15350.0   

             title_len  label0  label1  label2  label3  label4  label5  ...  \
subject                                                                 ...   
subject1272       12.0       1       2       2       1       0       1  ...   
subject2341        0.0       1       2       3       2       3       2  ...   
subject2432       63.0       1       3       3       2       3       2  ...   
subject2827      130.0       1       3       3       2       3       2  ...   
subject2903       12.0       0       0       1       1       0       0  ...   

             label11  label12  label13  label14  label15  label16  label17  \
subject                                                                      
subject1272        1        2        2        2       -3        0        3   
subject2341        2        3        3        2       -2        2       -3   
subject2432        3        1        3        2        1        2        1   
subject2827        1        2        3        1       -2        1        0   
subject2903        0        0        0        1        0        0       -1   

             label18  label19  label20  
subject                                 
subject1272        1        2        2  
subject2341        2        2        0  
subject2432        2        1        0  
subject2827        2        2        1  
subject2903        0        1        2  

[5 rows x 25 columns]

In [30]:
from sklearn.preprocessing import MultiLabelBinarizer

In [31]:
train_df['labels'] = train_df[['label%d'%i for i in range(21)]].values.tolist()
binarizer = MultiLabelBinarizer()
binarizer.fit([range(-3,3,1)])
# TODO: this is not the right way. it's not multilabel...?
train_df['labels'] = train_df['labels'].apply(lambda l: binarizer.transform((l,)))

/home/anasab/tftf3.6/local/lib/python3.6/site-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.
/home/anasab/tftf3.6/local/lib/python3.6/site-packages/sklearn/preprocessing/_label.py:987: UserWarning: unknown class(es) [3] will be ignored
  .format(sorted(unknown, key=str)))
/home/anasab/tftf3.6/local/lib/python3.6/site-packages/ipykernel_launcher.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """


In [32]:
train_df.head()

text  \
subject                                                          
subject1272   Just waking up every morning and talking to m...   
subject2341   If you need to talk to someone, it's not a ba...   
subject2432   *kid   A dataminer said that the octoling gir...   
subject2827   Im so sorry youve had a negative experience. ...   
subject2903   That was not at all how it was, but not gonna...   

                                                         title  text_len  \
subject                                                                    
subject1272                                                ...    1168.0   
subject2341                                                ...    6911.0   
subject2432                                                ...    7188.0   
subject2827           Opinions on high school anxiety      ...   17140.0   
subject2903                                                ...   15350.0   

             title_len  label0  label1  label2  label3  label4  label5  ...  \
subject                                                                 ...   
subject1272       12.0       1       2       2       1       0       1  ...   
subject2341        0.0       1       2       3       2       3       2  ...   
subject2432       63.0       1       3       3       2       3       2  ...   
subject2827      130.0       1       3       3       2       3       2  ...   
subject2903       12.0       0       0       1       1       0       0  ...   

             label12  label13  label14  label15  label16  label17  label18  \
subject                                                                      
subject1272        2        2        2       -3        0        3        1   
subject2341        3        3        2       -2        2       -3        2   
subject2432        1        3        2        1        2        1        2   
subject2827        2        3        1       -2        1        0        2   
subject2903        0        0        1        0        0       -1        0   

             label19  label20                labels  
subject                                              
subject1272        2        2  [[1, 0, 0, 1, 1, 1]]  
subject2341        2        0  [[1, 1, 0, 1, 1, 1]]  
subject2432        1        0  [[0, 0, 0, 1, 1, 1]]  
subject2827        2        1  [[0, 1, 0, 1, 1, 1]]  
subject2903        1        2  [[0, 0, 1, 1, 1, 1]]  

[5 rows x 26 columns]

In [33]:
args = {
#    'model_type':  'roberta',
#    'model_name': 'roberta-base',
   'output_dir': 'outputs/',
   'cache_dir': 'cache/',
    'fp16': True,
   'fp16_opt_level': 'O1',
   'max_seq_length': seq_len,#256, #128,
   'train_batch_size': 8,
   'eval_batch_size': 8,
   'gradient_accumulation_steps': 1,
   'num_train_epochs': 2,
   'weight_decay': 0,
   'learning_rate': 4e-6,
   'adam_epsilon': 1e-8,
   'warmup_ratio': 0.06,
   'warmup_steps': 0,
   'max_grad_norm': 1.0,
    'logging_steps': 50,
   'evaluate_during_training': True,
   'save_steps': 2000,
   'eval_all_checkpoints': False,
    'evaluate_during_training': True,
    'evaluate_during_training_verbose': True,
    'evaluate_during_training_steps': 3,
   'use_tensorboard': True,
#     'tensorboard_dir': 'tensorboard/',
    'overwrite_output_dir': True,
   'reprocess_input_data': False,
}

In [34]:
# Create a TransformerModel
model = MultiLabelClassificationModel('roberta', 'roberta-base', args=args)

In [ ]:
# Train the model
model.train_model(train_df=train_df, eval_df=test_df, text_ #acc=accuracy_score,
                                                          prec=precision_score,
                                                           f1=f1_score)#auto_weights=True)


# Extract features

In [28]:
hyperparams_features = {
    "max_features": 40000,
    # cut texts after this number of words
    # (among top max_features most common words)
    "maxlen": 512,
    "embedding_dim": 50,
    "user_level": True,
    "posts_per_user": 10,
    "batch_size": 2,
}

#### Emotions

In [29]:
def load_NRC(nrc_path):
    word_emotions = {}
    emotion_words = {}
    with open(nrc_path) as in_f:
        for line in in_f:
            line = line.strip()
            if not line:
                continue
            word, emotion, label = line.split()
            if word not in word_emotions:
                word_emotions[word] = set()
            if emotion not in emotion_words:
                emotion_words[emotion] = set()
            label = int(label)
            if label:
                word_emotions[word].add(emotion)
                emotion_words[emotion].add(word)
    return emotion_words

nrc_lexicon_path = root_dir + '/resources/NRC-Emotion-Lexicon-Wordlevel-v0.92.txt'
nrc_lexicon = load_NRC(nrc_lexicon_path)
emotions = list(nrc_lexicon.keys())


In [30]:
def encode_emotions(tokens, emotion_lexicon, emotions, relative=True):
    text_len = len(tokens)
    encoded_emotions = [0 for e in emotions]
    for i, emotion in enumerate(emotions):
        try:
            emotion_words = [t for t in tokens if t in emotion_lexicon[emotion]]
            if relative:
                encoded_emotions[i] = len(emotion_words) / len(tokens)
            else:
                encoded_emotions[i] = len(emotion_words)
        except ValueError:
            print("Emotion not found.")
    return encoded_emotions

In [31]:
from liwc_readDict import readDict

liwc = readDict(root_dir + '/resources/liwc.dic')

categories = set([c for (w,c) in liwc])
len(categories)

64

#### Personal pronouns

In [32]:
first_person_pronouns = {"i", "me", "my", "mine", "myself"}
def encode_pronouns(tokens, pronouns={"i", "me", "my", "mine", "myself"}, relative=True):
    if not tokens:
        return np.nan
    text_len = len(tokens)
    nr_pronouns = len([t for t in tokens if t in pronouns])
    if relative:
        return nr_pronouns/text_len
    else:
        return nr_pronouns

#### Stopwords

In [33]:
stopword_list = stopwords.words("english")
def encode_stopwords(tokens, stopwords=stopword_list):
    encoded_stopwords = [0 for s in stopword_list]
    if not tokens:
        return encoded_stopwords
    for i, stopword in enumerate(stopwords):
        if stopword in tokens:
            encoded_stopwords[i] += 1
    return encoded_stopwords

### BERT

In [33]:
# from easybert import Bert
# bert = Bert("https://tfhub.dev/google/bert_uncased_L-12_H-768_A-12/1")

In [34]:
# x = bert.embed("A sequence of words is a sequebce.")

In [35]:
# def encode_bert(sequence):
#     return bert.embed(sequence)

## Simple transformers


In [44]:
# import simpletransformers

In [45]:
# prefix='/home/anasab/eRisk/data/'
# train_df = pd.read_csv(prefix + 'train.csv', header=None)
# train_df.head()

# eval_df = pd.read_csv(prefix + 'test.csv', header=None)
# eval_df.head()

# train_df[0] = (train_df[0] == 2).astype(int)
# eval_df[0] = (eval_df[0] == 2).astype(int)

# train_df = pd.DataFrame({
#     'text': train_df[1].replace(r'\n', ' ', regex=True),
#     'label':train_df[0]
# })

# print(train_df.head())

# eval_df = pd.DataFrame({
#     'text': eval_df[1].replace(r'\n', ' ', regex=True),
#     'label':eval_df[0]
# })

# print(eval_df.head())

In [46]:
# from simpletransformers.classification import ClassificationModel


# # Create a TransformerModel
# model = ClassificationModel('roberta', 'roberta-base')

# # Train the model
# model.train_model(train_df)

# # Evaluate the model
# result, model_outputs, wrong_predictions = model.eval_model(eval_df)

In [47]:
# from bert import albert_tokenization
# from bert import bert_tokenization

In [36]:
import tensorflow_hub as hub
# bert_path = "https://tfhub.dev/google/bert_uncased_L-12_H-768_A-12/1"
bert_path = "https://tfhub.dev/tensorflow/bert_en_uncased_L-12_H-768_A-12/1"
import bert
from bert.tokenization.bert_tokenization import FullTokenizer

W0328 12:57:56.576619 140643282044672 __init__.py:56] Some hub symbols are not available because TensorFlow version is less than 1.14


ImportError: No module named 'bert.tokenization.bert_tokenization'; 'bert.tokenization' is not a package

In [49]:
bert_layer = hub.KerasLayer(bert_path,# signature='tokens' , signature_outputs_as_dict=True,
                            trainable=False)


INFO:absl:Using /tmp/tfhub_modules to cache modules.


InvalidArgumentError: assertion failed: [0] [Op:Assert] name: EagerVariableNameReuse

In [ ]:
class InputExample(object):
    """A single training/test example for simple sequence classification."""

    def __init__(self, guid, text_a, text_b=None, label=None):
        """Constructs a InputExample.
    Args:
      guid: Unique id for the example.
      text_a: string. The untokenized text of the first sequence. For single
        sequence tasks, only this sequence must be specified.
      text_b: (Optional) string. The untokenized text of the second sequence.
        Only must be specified for sequence pair tasks.
      label: (Optional) string. The label of the example. This should be
        specified for train and dev examples, but not for test examples.
    """
        self.guid = guid
        self.text_a = text_a
        self.text_b = text_b
        self.label = label

In [ ]:
def encode_text_for_bert(tokenizer, example, max_seq_length=512):
    """Converts a single `InputExample` into a single `InputFeatures`."""

#     if isinstance(example, PaddingInputExample):
#         input_ids = [0] * max_seq_length
#         input_mask = [0] * max_seq_length
#         segment_ids = [0] * max_seq_length
#         label = 0
#         return input_ids, input_mask, segment_ids, label

    tokens_a = tokenizer.tokenize(example.text_a)
    if len(tokens_a) > max_seq_length - 2:
        tokens_a = tokens_a[0 : (max_seq_length - 2)]

    tokens = []
    segment_ids = []
    tokens.append("[CLS]")
    segment_ids.append(0)
    for token in tokens_a:
        tokens.append(token)
        segment_ids.append(0)
    tokens.append("[SEP]")
    segment_ids.append(0)

    input_ids = tokenizer.convert_tokens_to_ids(tokens)

    # The mask has 1 for real tokens and 0 for padding tokens. Only real
    # tokens are attended to.
    input_mask = [1] * len(input_ids)

    # Zero-pad up to the sequence length.
    while len(input_ids) < max_seq_length:
        input_ids.append(0)
        input_mask.append(0)
        segment_ids.append(0)

    assert len(input_ids) == max_seq_length
    assert len(input_mask) == max_seq_length
    assert len(segment_ids) == max_seq_length

    return input_ids, input_mask, segment_ids, example.label


In [ ]:
def create_tokenizer_from_hub_module():
    """Get the vocab file and casing info from the Hub module."""
#     bert_module =  hub.Module(bert_path)
#     tokenization_info = bert_module(signature="tokenization_info", as_dict=True)
    vocab_file = bert_layer.resolved_object.vocab_file.asset_path.numpy()
    do_lower_case = bert_layer.resolved_object.do_lower_case.numpy()

#     vocab_file, do_lower_case = sess.run(
#         [
#             tokenization_info["vocab_file"],
#             tokenization_info["do_lower_case"],
#         ]
#     )

    return FullTokenizer(vocab_file=vocab_file, do_lower_case=do_lower_case)

In [ ]:
# Instantiate tokenizer
# bert_tokenizer = FullTokenizer()
bert_tokenizer = create_tokenizer_from_hub_module()

encode_text_for_bert(bert_tokenizer, InputExample(None, 
                                               "Ana are mere"), 
                       hyperparams_features['maxlen'])

### tfhub albert

In [ ]:
# input_ids = tf.keras.layers.Input(shape=[None], dtype=tf.int32)
# input_mask = tf.keras.layers.Input(shape=[None], dtype=tf.int32)
# sequence_mask = tf.keras.layers.Input(shape=[None], dtype=tf.int32)

# albert = hub.KerasLayer(
#     "https://tfhub.dev/google/albert_xlarge/3",
#     trainable=True,
#     signature="tokens",
#     output_key="pooled_output",
# )

# features = {
#     "input_ids": input_ids,
#     "input_mask": input_mask,
#     "segment_ids": sequence_mask,
# }
# out = albert(features)
# model = tf.keras.Model(inputs=[input_ids, input_mask, sequence_mask], outputs=out)
# model.compile("adam", loss="sparse_categorical_crossentropy")
# model.summary()

### Encode data

In [37]:
from collections import Counter
def encode_labels(labels):
    '''Convert ia to i and ib to -i'''
    encoded_labels = []
    for i, l in enumerate(labels):
        try:
            encoded_labels.append(int(l))
        except Exception as e:
            logger.debug("Encoding label %s\n" % l)
        
            if str(l)[-1] == 'a':
                encoded_labels.append(int(l[0]))
            elif str(l)[-1] == 'b':
                encoded_labels.append(-int(l[0]))
            else:
                logger.warning("Coult not encode label %s\n" % l)
    return encoded_labels

def load_erisk_data(writings_df, voc_size, emotion_lexicon, seq_len, emotions =  
                    ['anger', 'anticipation', 'disgust', 'fear', 'joy', 
                     'negative', 'positive', 'sadness', 'surprise', 'trust'],
                    liwc_categories = categories, ignore_features=[],
                    pronouns = ["i", "me", "my", "mine", "myself"],
                    train_prop=0.7, valid_prop=0.3, test_slice=2,
                    nr_slices=5,
                    min_post_len=3, min_word_len=1, 
                    user_level=True, vocabulary=None,
                   logger=logger):
    logger.debug("Loading data...\n")
    if not vocabulary:
        vocabulary = {}
        word_freqs = Counter()
        for words in writings_df.tokenized_text:
            word_freqs.update(words)
        for words in writings_df.tokenized_title:
            word_freqs.update(words)
        i = 1
        for w, f in word_freqs.most_common(voc_size-2): # keeping voc_size-1 for unk
            if len(w) < min_word_len:
                continue
            vocabulary[w] = i
            i += 1

    if 'subset' in writings_df.columns:
        training_subjects = list(set(writings_df[writings_df['subset']=='train'].subject))
        test_subjects = list(set(writings_df[writings_df['subset']=='test'].subject))
    else:
        all_subjects = sorted(list(set(writings_df.subject)))
        training_subjects_size = int(len(all_subjects) * train_prop)
        test_subjects_size = len(all_subjects) - training_subjects_size
        # Cross-validation, with fixed slice as input
        test_prop = 1-train_prop
        test_slice = min(test_slice, nr_slices)
        logger.debug("start index: %f, from %f\n" % (
            len(all_subjects)*(1/nr_slices)*test_slice, test_prop*test_slice))
        start_slice = int(len(all_subjects)*(1/nr_slices)*test_slice)
        test_subjects = all_subjects[start_slice: start_slice+test_subjects_size]
        training_subjects = [s for s in all_subjects if s not in test_subjects]
    training_subjects = sorted(training_subjects) # ensuring reproducibility
    valid_subjects_size = int(len(training_subjects) * valid_prop)
    valid_subjects = training_subjects[:valid_subjects_size]
    training_subjects = training_subjects[valid_subjects_size:]
    categories = [c for c in liwc_categories if c in writings_df.columns]
    logger.debug("%d training users, %d validation users, %d test users." % (
        len(training_subjects), 
          len(valid_subjects),
          len(test_subjects)))
    subjects_split = {'train': training_subjects, 
                      'valid': valid_subjects, 
                      'test': test_subjects}

    user_level_texts = {}
    for row in writings_df.sort_values(by='date').itertuples():
        words = []
        raw_text = ""
        if row.tokenized_title:
            words.extend(row.tokenized_title)
            raw_text += row.title
        if row.tokenized_text:
            words.extend(row.tokenized_text)
            raw_text += row.text
        if not words or len(words)<min_post_len:
            print(row.subject)
            continue
        labels = [getattr(row, 'label%d'%i) for i in range(nr_questions)]
        liwc_categs = [getattr(row, categ) for categ in categories]
        if row.subject not in user_level_texts.keys():
            user_level_texts[row.subject] = {}
            user_level_texts[row.subject]['texts'] = [words]
            user_level_texts[row.subject]['labels'] = encode_labels(labels)
            user_level_texts[row.subject]['liwc'] = [liwc_categs]
            user_level_texts[row.subject]['raw'] = [raw_text]
        else:
            user_level_texts[row.subject]['texts'].append(words)
            user_level_texts[row.subject]['liwc'].append(liwc_categs)
            user_level_texts[row.subject]['raw'].append(raw_text)

    return user_level_texts, subjects_split, vocabulary


In [38]:
user_level_data, subjects_split, vocabulary = load_erisk_data(writings_df, 
                                                            seq_len=hyperparams_features['maxlen'],
                                                            voc_size=hyperparams_features['max_features'],
                                                           emotion_lexicon=nrc_lexicon,
                                                           emotions=emotions,
                                                           user_level=hyperparams_features['user_level'],
                                                                                logger=logger,
                                                           vocabulary=pickle.load(open('vocabulary_40K_all.pkl', 'rb'))
                                                                               )

Loading data...



I0328 12:58:08.486985 140643282044672 <ipython-input-37-ed5a3d9938b1>:29] Loading data...



start index: 8.000000, from 0.600000



I0328 12:58:08.488625 140643282044672 <ipython-input-37-ed5a3d9938b1>:55] start index: 8.000000, from 0.600000



10 training users, 4 validation users, 6 test users.


I0328 12:58:08.489387 140643282044672 <ipython-input-37-ed5a3d9938b1>:67] 10 training users, 4 validation users, 6 test users.


subject3993
subject3993
subject3993
subject9798
subject9798
subject9798
subject9798
subject9798
subject9798
subject9798
subject9798
subject2903
subject9798
subject6619
subject2903
subject2903
subject9798
subject6619
subject6619
subject6619
subject6619
subject6619
subject6619
subject6619
subject6619
subject6619
subject6619
subject3993
subject5791
subject6619
subject5791
subject9798
subject6619
subject9798
subject6619
subject6619
subject6619
subject6619
subject6619
subject6619
subject5791
subject7039
subject5791
subject5791
subject6619
subject6619
subject6619
subject6619
subject6619
subject6635
subject6619
subject6635
subject6619
subject6635
subject6635
subject7039
subject3993
subject6635
subject6619
subject7039
subject9694
subject6619
subject7039
subject7039
subject7039
subject7039
subject7039
subject7039
subject7039
subject7039
subject7039
subject6619
subject7039
subject9694
subject6635
subject6635
subject7039
subject9694
subject9694
subject9694
subject9694
subject9694
subject7039
subj

subject2827
subject9798
subject9454
subject9454
subject9454
subject2961
subject2827
subject9454
subject9218
subject9218
subject9218
subject9218
subject2432
subject9454
subject9798
subject6900
subject2961
subject2961
subject2961
subject9454
subject2827
subject2827
subject9218
subject2827
subject2827
subject9218
subject2827
subject2961
subject9218
subject9798
subject5897
subject9694
subject9218
subject2827
subject9218
subject2827
subject9218
subject9694
subject2432
subject2827
subject9454
subject2432
subject2961
subject9218
subject9694
subject2961
subject2432
subject9454
subject2432
subject9694
subject9694
subject9694
subject9694
subject9694
subject9694
subject9694
subject9798
subject2827
subject2432
subject9798
subject9694
subject6900
subject9798
subject3993
subject9694
subject6900
subject6900
subject6900
subject6900
subject9798
subject3993
subject9694
subject6900
subject9694
subject9694
subject2903
subject4058
subject3707
subject3707
subject9694
subject9694
subject9694
subject9798
subj

In [39]:
user_level_data['subject6900']['labels']

[1, 1, 2, 1, 0, 0, 1, 1, 1, 1, 1, 1, 0, 1, 2, 2, 0, 0, 0, 1, 0]

In [40]:
def load_embeddings(path, embedding_dim, voc):
    # random matrix with mean value = 0
    embedding_matrix = np.random.random((len(voc)+2, embedding_dim)) - 0.5 # voc + unk + pad value(0)

    f = open(path)
    for line in f:
        values = line.split()
        word = values[0]
        coefs = np.asarray(values[1:], dtype='float32')
        word_i = voc.get(word)
        if word_i is not None:
            embedding_matrix[word_i] = coefs
    f.close()

    print('Total %s word vectors.' % len(embedding_matrix))

 
    return embedding_matrix

pretrained_embeddings_path = root_dir + '/resources/glove.twitter.27B/glove.twitter.27B.%dd.txt' % hyperparams_features['embedding_dim']
embedding_matrix = load_embeddings(pretrained_embeddings_path, hyperparams_features['embedding_dim'], vocabulary)


Total 40000 word vectors.


## Data Generator

In [41]:
class DataGenerator(Sequence):
    'Generates data for Keras'
    def __init__(self, user_level_data, subjects_split, set_type='train', bert_tokenizer=bert_tokenizer,
                 batch_size=hyperparams_features['batch_size'], seq_len=hyperparams_features['maxlen'], 
                 voc_size=hyperparams_features['max_features'], emotion_lexicon=nrc_lexicon,
                 emotions=emotions, pronouns=["i", "me", "my", "mine", "myself"], 
                 max_posts_per_user=hyperparams_features['posts_per_user'],
                 shuffle=True):
        'Initialization'
        self.seq_len = seq_len
        self.bert_tokenizer = bert_tokenizer
        self.subjects_split = subjects_split
        self.set = set_type
        self.emotion_lexicon = emotion_lexicon
        self.batch_size = batch_size
        self.data = user_level_data
        self.emotions = emotions
        self.pronouns = pronouns
        self.shuffle = shuffle
        self.voc_size = voc_size
        self.max_posts_per_user = max_posts_per_user
        self.on_epoch_end()

    def __encode_text(self, tokens, raw_text):
        # Using voc_size-1 value for OOV token
        encoded_tokens = [vocabulary.get(w, self.voc_size-1) for w in tokens]
        encoded_emotions = encode_emotions(tokens, self.emotion_lexicon, self.emotions)
        encoded_pronouns = encode_pronouns(tokens, self.pronouns)
        encoded_stopwords = encode_stopwords(tokens)
        bert_ids, bert_masks, bert_segments, label = encode_text_for_bert(self.bert_tokenizer, InputExample(None, 
                                               raw_text), self.seq_len)
        return (encoded_tokens, encoded_emotions, encoded_pronouns, encoded_stopwords,
               bert_ids, bert_masks, bert_segments)
        
    def __len__(self):
        'Denotes the number of batches per epoch'
        return int(np.floor(len(self.subjects_split[self.set]) / self.batch_size))

    def __getitem__(self, index):
        'Generate one batch of data'
        # Generate indexes of the batch
        user_indexes = self.indexes[index*self.batch_size:(index+1)*self.batch_size]
        # Find users
        users = [self.subjects_split[self.set][i] for i in user_indexes
                    if self.subjects_split[self.set][i] in self.data.keys()] # TODO: maybe needs a warning that user is missing

        post_indexes = {}
        # Sample post ids
        for subject in users:
            posts_len = len(self.data[subject]['texts'])
            posts_index_sample = sorted(np.random.choice(posts_len, 
                                                         min(self.max_posts_per_user, posts_len),
                                                         replace=False))
            post_indexes[subject] = posts_index_sample
        # Generate data
        X, y = self.__data_generation(users, post_indexes)

        return X, y

    def on_epoch_end(self):
        'Updates indexes after each epoch'
        self.indexes = np.arange(len(self.subjects_split[self.set]))
        if self.shuffle == True:
            np.random.shuffle(self.indexes)

    def __data_generation(self, users, post_indexes):
        'Generates data containing batch_size samples' # X : (n_samples, *dim, n_channels)
        tokens_data = []
        categ_data = []
        sparse_data = []
        subjects = []
        bert_ids_data = []
        bert_masks_data = []
        bert_segments_data = []
        labels = []

        for subject in users:
            texts = self.data[subject]['texts']
            raw_texts = self.data[subject]['raw']
            label = self.data[subject]['label']
            liwc_scores = self.data[subject]['liwc']
            
            # Sample
            texts = [texts[i] for i in post_indexes[subject]]
            liwc_selection = [liwc_scores[i] for i in post_indexes[subject]]
            raw_texts = [raw_texts[i] for i in post_indexes[subject]]
            
            all_words = [sum(texts, [])] # merge all texts in one list -- Ok, why sum?? this is wrong!!
            liwc_aggreg = [np.array(liwc_selection).mean(axis=0).tolist()]
            all_raw_texts = [" ".join(raw_texts)]
            
            for i, words in enumerate(all_words):
                encoded_tokens, encoded_emotions, encoded_pronouns, encoded_stopwords, \
                    bert_ids, bert_masks, bert_segments = self.__encode_text(words, all_raw_texts[i])
                subject_id = int(subject.split('t')[1])
                tokens_data.append(encoded_tokens)
                categ_data.append(encoded_emotions + [encoded_pronouns] + liwc_aggreg[i])
                sparse_data.append(encoded_stopwords)
                bert_ids_data.append(bert_ids)
                bert_masks_data.append(bert_masks)
                bert_segments_data.append(bert_segments)
                
                labels.append(label)
                subjects.append(subject_id)

        
        # using zeros for padding
        tokens_data_padded = sequence.pad_sequences(tokens_data, maxlen=self.seq_len)

        return ([np.array(tokens_data_padded), np.array(categ_data), np.array(sparse_data),
                 np.array(bert_ids_data), np.array(bert_masks_data), np.array(bert_segments_data),
                np.array(subjects)],
                np.array(labels))

NameError: name 'bert_tokenizer' is not defined

In [ ]:
class DataGenerator(Sequence):
    'Generates data for Keras'
    def __init__(self, user_level_data, subjects_split, batch_size=hyperparams_features['batch_size'], 
                 seq_len=hyperparams_features['maxlen'], voc_size=hyperparams_features['max_features'], 
                 emotion_lexicon=nrc_lexicon, set_type='train', test_user_indexes=[0],
                 emotions=emotions, pronouns=["i", "me", "my", "mine", "myself"], 
                 max_posts_per_user=hyperparams_features['posts_per_user'],
                 bert_tokenizer=bert_tokenizer,
                 shuffle=True):
        'Initialization'
        self.seq_len = seq_len
        self.emotion_lexicon = emotion_lexicon
        self.bert_tokenizer = bert_tokenizer
        self.batch_size = batch_size
        self.data = user_level_data
        self.all_users = list(self.data.keys())
        self.emotions = emotions
        self.pronouns = pronouns
        self.set = set_type
        self.subjects_split = subjects_split
        self.shuffle = shuffle
        self.voc_size = voc_size
        self.max_posts_per_user = max_posts_per_user
        self.test_user_indexes = test_user_indexes
        self.on_epoch_end()


    def __encode_text(self, tokens, raw_text):
        # Using voc_size-1 value for OOV token
        encoded_tokens = [vocabulary.get(w, self.voc_size-1) for w in tokens]
        encoded_emotions = encode_emotions(tokens, self.emotion_lexicon, self.emotions)
        encoded_pronouns = encode_pronouns(tokens, self.pronouns)
        encoded_stopwords = encode_stopwords(tokens)
        bert_ids, bert_masks, bert_segments, label = encode_text_for_bert(self.bert_tokenizer, InputExample(None, 
                                               raw_text), self.seq_len)
        return (encoded_tokens, encoded_emotions, encoded_pronouns, encoded_stopwords,
               bert_ids, bert_masks, bert_segments)
        
    def __len__(self):
        'Denotes the number of batches per epoch'
        return int(np.floor(len(self.subjects_split[self.set]) / self.batch_size))

    def __getitem__(self, index):
        'Generate one batch of data'
        # Generate indexes of the batch
        user_indexes = self.indexes[index*self.batch_size:(index+1)*self.batch_size]
        # Find users
        users = [self.subjects_split[self.set][i] for i in user_indexes
                    if self.subjects_split[self.set][i] in self.data.keys()] # TODO: maybe needs a warning that user is missing

        post_indexes = {}
        # Sample post ids
        for subject in users:
            posts_len = len(self.data[subject]['texts'])
            posts_index_sample = sorted(np.random.choice(posts_len, 
                                                         min(self.max_posts_per_user, posts_len),
                                                         replace=False))
            post_indexes[subject] = posts_index_sample
        # Generate data
        X, y = self.__data_generation(users, post_indexes)

        return X, y

    def on_epoch_end(self):
        'Updates indexes after each epoch'
        self.indexes = np.arange(len(self.subjects_split[self.set]))
        if self.shuffle == True:
            np.random.shuffle(self.indexes)

    def __data_generation(self, users, post_indexes):
        'Generates data containing batch_size samples' # X : (n_samples, *dim, n_channels)
        tokens_data = []
        categ_data = []
        sparse_data = []
        subjects = []
        bert_ids_data = []
        bert_masks_data = []
        bert_segments_data = []
        labels = []
        for subject in users:
            texts = self.data[subject]['texts']
            label = self.data[subject]['labels']
            raw_texts = self.data[subject]['raw']

            # Sample
            texts = [texts[i] for i in post_indexes[subject]]
            liwc_selection = [self.data[subject]['liwc'][i] for i in post_indexes[subject]]
            raw_texts = [raw_texts[i] for i in post_indexes[subject]]

            all_words = [sum(texts, [])] # merge all texts in one list
            liwc_aggreg = [np.array(liwc_selection).mean(axis=0).tolist()]
            all_raw_texts = [" ".join(raw_texts)]

            
            for i, words in enumerate(all_words):
                encoded_tokens, encoded_emotions, encoded_pronouns, encoded_stopwords, \
                    bert_ids, bert_masks, bert_segments = self.__encode_text(words, all_raw_texts[i])
                subject_id = int(subject.split('t')[1])
                tokens_data.append(encoded_tokens)
                categ_data.append(encoded_emotions + [encoded_pronouns] + liwc_aggreg[i])
                sparse_data.append(encoded_stopwords)
                labels.append(label)
                bert_ids_data.append(bert_ids)
                bert_masks_data.append(bert_masks)
                bert_segments_data.append(bert_segments)
                
                subjects.append(subject_id)

        
        # using zeros for padding
        tokens_data_padded = sequence.pad_sequences(tokens_data, maxlen=self.seq_len)

        return ([np.array(tokens_data_padded), np.array(categ_data), np.array(sparse_data),
#                 np.array(subjects),
                np.array(bert_ids_data, dtype=np.int32), 
                 np.array(bert_masks_data, dtype=np.int32), 
                 np.array(bert_segments_data, dtype=np.int32),],
                np.array(labels))
#                 np.array(labels).reshape(self.batch_size, -1, len(labels)).tolist()) # to have one array per output

In [ ]:
# TODO: Don't split into the 3 sets, do leave-one-out cross-validation

In [ ]:
def get_subjects_split(test_size=hyperparams_features['batch_size']):
    test_user_indexes = [np.random.randint(len(user_level_data)) for i in range(test_size)]

    subjects_split = {'test': [u for i,u in 
                               enumerate(user_level_data.keys()) if i in test_user_indexes],
                     'train': [u for i,u in 
                               enumerate(user_level_data.keys()) if i not in test_user_indexes],}
    return subjects_split

In [ ]:
logger.setLevel(logging.DEBUG)

# TODO: it is skipping the last batch
x_data = {'train': [], 'test': []}
y_data = {'train': [], 'test': []}
subjects_split = get_subjects_split()
for set_type in ['train', 'test']:
    for x, y in DataGenerator(user_level_data, batch_size=hyperparams_features['batch_size'],
                            set_type=set_type,
                             subjects_split=subjects_split):
        print(x)
        x_data[set_type].append(x)
        y_data[set_type].append(y)
#         break


In [ ]:
y_data['test'][0]

In [ ]:
x_data['train'][0][5].shape

In [ ]:
np.array([[1,2],[3,4]]).reshape(2,-1)

In [ ]:
sum([len(subjects_split[s]) for s in ['train', 'test']])

In [ ]:
x_data['train']

In [ ]:
y_data

# Train

In [ ]:
hyperparams = {
    'lstm_units': 10,
    'dense_bow_units': 20,
    'dropout': 0.0,
    'l2_dense': 0.00000011,
    'l2_embeddings': 0.000001,
    'dense_sentence_units': 100,
    'optimizer': 'adam',
    'bert_dense_units': 256,
    'decay': 0.00001,
    'lr': 0.01,
    "trainable_embeddings": False,
    "reduce_lr_factor": 0.0002,
    "reduce_lr_patience": 1000,
    "freeze_patience": 500,
    'threshold': 0.5,
    'bert_len': 768,
    'ignore_layer': ['batchnorm', 'lstm_layers', 'numerical_dense_layer', 'sparse_feat_dense_layer'],
    'norm_momentum': 0.1,

}
if not hyperparams['optimizer']:
    hyperparams['optimizer'] = optimizers.Adam(lr=hyperparams['lr'], #beta_1=0.9, beta_2=0.999, epsilon=0.0001,
                                   decay=hyperparams['decay'])

In [ ]:
# class Metrics():
#     def __init__(self, threshold=0.5):
#         self.threshold=threshold
        
#     def recall_m(self, y_true, y_pred):
#             y_labels = y_true
#             y_pred = K.cast(K.greater(K.clip(y_pred, 0, 1), self.threshold), K.floatx())        
#             possible_positives = K.sum(K.round(K.clip(y_labels, 0, 1)))
#             true_positives = K.sum(K.round(K.clip(y_labels * y_pred, 0, 1)))
#             recall = true_positives / (possible_positives + K.epsilon())
#             return recall

#     def precision_m(self, y_true, y_pred):
#             y_labels = y_true
#             y_pred = K.cast(K.greater(K.clip(y_pred, 0, 1), self.threshold), K.floatx())        
#             true_positives = K.sum(K.round(K.clip(y_labels * y_pred, 0, 1)))
#             predicted_positives = K.sum(K.round(K.clip(y_pred, 0, 1)))
#             precision = true_positives / (predicted_positives + K.epsilon())
#             return precision

#     def f1_m(self, y_true, y_pred):
#         precision = self.precision_m(y_true, y_pred)
#         recall = self.recall_m(y_true, y_pred)
#         return 2*((precision*recall)/(precision+recall+K.epsilon()))

# def binary_crossentropy_custom(y_true, y_pred):
#     y_labels = y_true
#     return K.binary_crossentropy(y_labels, 
#                                  y_pred)

# metrics_class = Metrics(threshold=hyperparams['threshold'])

In [ ]:
def build_model(hyperparams, hyperparams_features, embedding_matrix, emotions, stopwords_list,
                liwc_categories, nr_classes,
               ignore_layer=[]):

    tokens_features = Input(shape=(hyperparams_features['maxlen'],), name='word_seq')
    embedding_layer = Embedding(hyperparams_features['max_features'], 
                                hyperparams_features['embedding_dim'], 
                                input_length=hyperparams_features['maxlen'],
                                embeddings_regularizer=regularizers.l2(hyperparams['l2_embeddings']),
                                weights=[embedding_matrix], 
                                trainable=hyperparams['trainable_embeddings'],
                               name='embeddings_layer')(
        tokens_features)
#     if 'batchnorm' not in ignore_layer:
#         embedding_layer_norm = BatchNormalization(axis=-1, momentum=hyperparams['norm_momentum'],
#                                                      name='embeddings_layer_norm')(embedding_layer)
#     lstm_layers = Bidirectional(LSTM(hyperparams['lstm_units']))(embedding_layer)


    lstm_layers = LSTM(hyperparams['lstm_units'], 
                           return_sequences='attention' not in ignore_layer,
                      name='LSTM_layer')(embedding_layer)
    
    # Attention
    if 'attention' not in ignore_layer:
        attention = Dense(1, activation='tanh', name='attention')(lstm_layers)
        attention = Flatten()(attention)
        attention = Activation('softmax')(attention)
        attention = RepeatVector(hyperparams['lstm_units'])(attention)
        attention = Permute([2, 1])(attention)

        sent_representation = Multiply()([lstm_layers, attention])
        sent_representation = Lambda(lambda xin: K.sum(xin, axis=1), 
                                     output_shape=(hyperparams['lstm_units'],)
                                    )(sent_representation)

        
    else:
        sent_representation = lstm_layers
        
    
    sent_representation = Dropout(hyperparams['dropout'], name='lstm_att_dropout')(sent_representation)
    if hyperparams['dense_sentence_units']:
        sent_representation = Dense(units=hyperparams['dense_sentence_units'],
                                   name='dense_sent_representation')(sent_representation)
    numerical_features = Input(shape=(len(emotions) + 1 + len(liwc_categories),), name='numeric_input') # emotions and pronouns
    
    in_id_bert = Input(shape=(hyperparams_features['maxlen'],), dtype='int32', name="input_ids_bert")
    in_mask_bert = Input(shape=(hyperparams_features['maxlen'],), dtype='int32', name="input_masks_bert")
    in_segment_bert = Input(shape=(hyperparams_features['maxlen'],), dtype='int32', name="segment_ids_bert")
#     bert_layer = hub.Module(
#         "https://tfhub.dev/google/albert_xlarge/3",
#         bert_path, trainable=True,
#         trainable=False,
#         signature="tokens",
#         signature_outputs_as_dict=True,
#         output_key="pooled_output",
#     )

#     bert_layer = hub.Module(
# #         "https://tfhub.dev/google/albert_xlarge/3",
#         bert_path, trainable=True,
# #         trainable=False,
# #         signature="tokens",
# #         signature_outputs_as_dict=True,
#         output_key="pooled_output",
#     )

    albert = hub.KerasLayer(
        "https://tfhub.dev/google/albert_base/3",
        trainable=False,
        signature="tokens",
        output_key="pooled_output",
    )

    bert_features = {
        "input_ids": in_id_bert,
        "input_mask": in_mask_bert,
        "segment_ids": in_segment_bert,
    }
    bert_output = albert(bert_features)
#     bert_output = albert([in_id_bert, in_mask_bert, in_segment_bert])['pooled_output']  # TODO: can also be 'mean'. Check BertLayer
    dense_layer_bert = Dense(units=hyperparams['bert_dense_units'],
                        kernel_regularizer=regularizers.l2(hyperparams['l2_dense']),
                        name='bert_dense_layer',
                       )(bert_output)
    sparse_features = Input(shape=(len(stopwords_list),), name='sparse_input') # stopwords

    if hyperparams['dense_bow_units']:
        dense_layer_sparse = Dense(units=hyperparams['dense_bow_units'],
                              name='sparse_feat_dense_layer',
                                kernel_regularizer=regularizers.l2(hyperparams['l2_dense']),
                              )(sparse_features)
    else:
        dense_layer_sparse = sparse_features
    
    if 'batchnorm' not in ignore_layer:
        numerical_features_norm = BatchNormalization(axis=1, momentum=hyperparams['norm_momentum'],
                                                     name='numerical_features_norm')(numerical_features)
        sent_representation_norm = BatchNormalization(axis=1, momentum=hyperparams['norm_momentum'],
                                                      name='sent_repr_norm')(sent_representation)

        dense_layer_sparse_norm = BatchNormalization(axis=1, momentum=hyperparams['norm_momentum'],
                                                         name='sparse_features_norm')(dense_layer_sparse)
        dense_layer_bert_norm = BatchNormalization(axis=1, momentum=hyperparams['norm_momentum'],
                                                         name='bert_features_norm')(dense_layer_bert)
        
    subjects = Input(shape=(1,), name='subjects')
    

    all_layers = {
        'lstm_layers': sent_representation,
        'numerical_dense_layer': numerical_features,
        'sparse_feat_dense_layer': dense_layer_sparse,
        'bert_layer': dense_layer_bert
    }
    if 'batchnorm' not in ignore_layer:
        all_layers = {
            'lstm_layers': sent_representation_norm,
            'numerical_dense_layer': numerical_features_norm,
            'sparse_feat_dense_layer': dense_layer_sparse_norm,
            'bert_layer': dense_layer_bert_norm
        }
    layers_to_merge = []
    for n, l in all_layers.items():
        if n in ignore_layer:
            continue
        layers_to_merge.append(l)
        
    if len(layers_to_merge) == 1:
        merged_layers = layers_to_merge[0]
    else:
        merged_layers = concatenate(layers_to_merge)
    output_layers = []
    for label in range(nr_classes):
        output_layer = Dense(1, activation='softmax',
                         name='output_layer%d' % label,
                        kernel_regularizer=regularizers.l2(hyperparams['l2_dense']))(merged_layers)
        output_layers.append(output_layer)

    # Compile model
    model = Model(inputs=[tokens_features, numerical_features, sparse_features,
                         in_id_bert, in_mask_bert, in_segment_bert], 
                  outputs=output_layers)

    model.compile(hyperparams['optimizer'], {'output_layer%d'%i: 
                                             'mean_squared_error' for i in range(nr_classes)},
                  metrics={'output_layer%d' % label: 
                           ['accuracy', 'mean_squared_error'] for label in range(nr_classes)})
    return model



In [ ]:
hub.KerasLayer

In [507]:
model = build_model(hyperparams, hyperparams_features, embedding_matrix, emotions, stopword_list,
                    liwc_categories=[c for c in categories if c in writings_df.columns],
                    nr_classes=nr_questions,
                   ignore_layer=hyperparams['ignore_layer'])
model.summary()

Model: "model_4"
__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_ids_bert (InputLayer)     [(None, 512)]        0                                            
__________________________________________________________________________________________________
input_masks_bert (InputLayer)   [(None, 512)]        0                                            
__________________________________________________________________________________________________
segment_ids_bert (InputLayer)   [(None, 512)]        0                                            
__________________________________________________________________________________________________
keras_layer_7 (KerasLayer)      (None, 768)          11812272    input_ids_bert[0][0]             
                                                                 input_masks_bert[0][0]     

In [508]:
def train_model(model, 
                data_generator_train, data_generator_valid,
                epochs, start_epoch=0, workers=4,
                callback_list = [],
                model_path='/tmp/model',
               verbose=1):
    logging.info('Train...')
    experiment.log_parameter('callbacks', callbacks)

    history = model.fit_generator(data_generator_train,
#               batch_size=batch_size,
#                 steps_per_epoch=steps_per_epoch,
              epochs=epochs, initial_epoch=start_epoch, 
              validation_data=data_generator_valid,
                        verbose=verbose,
#               validation_split=0.3,
                       workers=workers,
            callbacks = [
                callbacks.ModelCheckpoint(filepath='%s_best' % model_path, verbose=1, 
                                          save_best_only=True),
                callbacks.EarlyStopping(patience=500), *callback_list
            ])
    model.save(model_path)
    experiment.log_parameter('model_path', model_path)
    return model, history

In [509]:
experiment = Experiment(api_key="eoBdVyznAhfg3bK9pZ58ZSXfv",
                        project_name="mental", workspace="ananana", disabled=False)

experiment.log_parameters(hyperparams_features)

experiment.log_parameter('emotion_lexicon', nrc_lexicon_path)
experiment.log_parameter('emotions', emotions)
experiment.log_parameter('embeddings_path', pretrained_embeddings_path)

experiment.add_tag('T2')
experiment.log_parameters(hyperparams)

COMET INFO: ----------------------------
COMET INFO: Comet.ml Experiment Summary:
COMET INFO:   Data:
COMET INFO:     url: https://www.comet.ml/ananana/mental/99e269aaa3a94ad8b84a9645288489cf
COMET INFO:   Metrics [count] (min, max):
COMET INFO:     batch_loss [803]                                      : (16.0, 63.000038146972656)
COMET INFO:     batch_output_layer0_accuracy [803]                    : (0.0714285746216774, 0.6190476417541504)
COMET INFO:     batch_output_layer0_loss [803]                        : (0.761904776096344, 3.0)
COMET INFO:     batch_output_layer0_mean_squared_error [803]          : (0.761904776096344, 3.0)
COMET INFO:     batch_output_layer10_accuracy [803]                   : (0.0714285746216774, 0.6190476417541504)
COMET INFO:     batch_output_layer10_loss [803]                       : (0.761904776096344, 3.0)
COMET INFO:     batch_output_layer10_mean_squared_error [803]         : (0.761904776096344, 3.0)
COMET INFO:     batch_output_layer11_accuracy [803]  

COMET INFO:     output_layer12_mean_squared_error [803]               : (1.3531745672225952, 1.5555557012557983)
COMET INFO:     output_layer13_accuracy [803]                         : (0.2460317462682724, 0.2976190745830536)
COMET INFO:     output_layer13_loss [803]                             : (1.3531745672225952, 1.5555557012557983)
COMET INFO:     output_layer13_mean_squared_error [803]               : (1.3531745672225952, 1.5555557012557983)
COMET INFO:     output_layer14_accuracy [803]                         : (0.2460317462682724, 0.2976190745830536)
COMET INFO:     output_layer14_loss [803]                             : (1.3531745672225952, 1.5555557012557983)
COMET INFO:     output_layer14_mean_squared_error [803]               : (1.3531745672225952, 1.5555557012557983)
COMET INFO:     output_layer15_accuracy [803]                         : (0.2460317462682724, 0.2976190745830536)
COMET INFO:     output_layer15_loss [803]                             : (1.3531745672225952, 1.5

COMET INFO:     val_output_layer0_accuracy [803]                      : (0.2460317462682724, 0.3174603283405304)
COMET INFO:     val_output_layer0_loss [803]                          : (1.29365074634552, 1.5476192235946655)
COMET INFO:     val_output_layer0_mean_squared_error [803]            : (1.29365074634552, 1.5476192235946655)
COMET INFO:     val_output_layer10_accuracy [803]                     : (0.2460317462682724, 0.3174603283405304)
COMET INFO:     val_output_layer10_loss [803]                         : (1.29365074634552, 1.5476192235946655)
COMET INFO:     val_output_layer10_mean_squared_error [803]           : (1.29365074634552, 1.5476192235946655)
COMET INFO:     val_output_layer11_accuracy [803]                     : (0.2460317462682724, 0.3174603283405304)
COMET INFO:     val_output_layer11_loss [803]                         : (1.29365074634552, 1.5476192235946655)
COMET INFO:     val_output_layer11_mean_squared_error [803]           : (1.29365074634552, 1.5476192235946

COMET INFO:     validate_batch_output_layer12_mean_squared_error [803]: (0.6904761791229248, 2.0)
COMET INFO:     validate_batch_output_layer13_accuracy [803]          : (0.1428571492433548, 0.4285714626312256)
COMET INFO:     validate_batch_output_layer13_loss [803]              : (0.6904761791229248, 2.0)
COMET INFO:     validate_batch_output_layer13_mean_squared_error [803]: (0.6904761791229248, 2.0)
COMET INFO:     validate_batch_output_layer14_accuracy [803]          : (0.1428571492433548, 0.4285714626312256)
COMET INFO:     validate_batch_output_layer14_loss [803]              : (0.6904761791229248, 2.0)
COMET INFO:     validate_batch_output_layer14_mean_squared_error [803]: (0.6904761791229248, 2.0)
COMET INFO:     validate_batch_output_layer15_accuracy [803]          : (0.1428571492433548, 0.4285714626312256)
COMET INFO:     validate_batch_output_layer15_loss [803]              : (0.6904761791229248, 2.0)
COMET INFO:     validate_batch_output_layer15_mean_squared_error [803]: (

In [510]:
subjects_split = get_subjects_split(test_size=10)
data_generator_train = DataGenerator(user_level_data, set_type='train', 
                                     subjects_split=subjects_split)
data_generator_valid = DataGenerator(user_level_data, set_type='test',  
                                     subjects_split=subjects_split)
model, history = train_model(model, data_generator_train, data_generator_valid,
           epochs=1000, start_epoch=0,
                      callback_list = [],
                      model_path='models/bert_t21', workers=1)

Epoch 1/1000
6/6 [==============================] - ETA: 0s - loss: 32.4167 - output_layer0_loss: 1.5437 - output_layer1_loss: 1.5437 - output_layer2_loss: 1.5437 - output_layer3_loss: 1.5437 - output_layer4_loss: 1.5437 - output_layer5_loss: 1.5437 - output_layer6_loss: 1.5437 - output_layer7_loss: 1.5437 - output_layer8_loss: 1.5437 - output_layer9_loss: 1.5437 - output_layer10_loss: 1.5437 - output_layer11_loss: 1.5437 - output_layer12_loss: 1.5437 - output_layer13_loss: 1.5437 - output_layer14_loss: 1.5437 - output_layer15_loss: 1.5437 - output_layer16_loss: 1.5437 - output_layer17_loss: 1.5437 - output_layer18_loss: 1.5437 - output_layer19_loss: 1.5437 - output_layer20_loss: 1.5437 - output_layer0_accuracy: 0.3056 - output_layer0_mean_squared_error: 1.5437 - output_layer1_accuracy: 0.3056 - output_layer1_mean_squared_error: 1.5437 - output_layer2_accuracy: 0.3056 - output_layer2_mean_squared_error: 1.5437 - output_layer3_accuracy: 0.3056 - output_layer3_mean_squared_error: 1.5437 

INFO:tensorflow:Assets written to: models/bert_t21_best/assets


6/6 [==============================] - 8s 1s/step - loss: 32.4167 - output_layer0_loss: 1.5437 - output_layer1_loss: 1.5437 - output_layer2_loss: 1.5437 - output_layer3_loss: 1.5437 - output_layer4_loss: 1.5437 - output_layer5_loss: 1.5437 - output_layer6_loss: 1.5437 - output_layer7_loss: 1.5437 - output_layer8_loss: 1.5437 - output_layer9_loss: 1.5437 - output_layer10_loss: 1.5437 - output_layer11_loss: 1.5437 - output_layer12_loss: 1.5437 - output_layer13_loss: 1.5437 - output_layer14_loss: 1.5437 - output_layer15_loss: 1.5437 - output_layer16_loss: 1.5437 - output_layer17_loss: 1.5437 - output_layer18_loss: 1.5437 - output_layer19_loss: 1.5437 - output_layer20_loss: 1.5437 - output_layer0_accuracy: 0.3056 - output_layer0_mean_squared_error: 1.5437 - output_layer1_accuracy: 0.3056 - output_layer1_mean_squared_error: 1.5437 - output_layer2_accuracy: 0.3056 - output_layer2_mean_squared_error: 1.5437 - output_layer3_accuracy: 0.3056 - output_layer3_mean_squared_error: 1.5437 - output_l

INFO:tensorflow:Assets written to: models/bert_t21_best/assets


6/6 [==============================] - 6s 1s/step - loss: 32.4167 - output_layer0_loss: 1.5437 - output_layer1_loss: 1.5437 - output_layer2_loss: 1.5437 - output_layer3_loss: 1.5437 - output_layer4_loss: 1.5437 - output_layer5_loss: 1.5437 - output_layer6_loss: 1.5437 - output_layer7_loss: 1.5437 - output_layer8_loss: 1.5437 - output_layer9_loss: 1.5437 - output_layer10_loss: 1.5437 - output_layer11_loss: 1.5437 - output_layer12_loss: 1.5437 - output_layer13_loss: 1.5437 - output_layer14_loss: 1.5437 - output_layer15_loss: 1.5437 - output_layer16_loss: 1.5437 - output_layer17_loss: 1.5437 - output_layer18_loss: 1.5437 - output_layer19_loss: 1.5437 - output_layer20_loss: 1.5437 - output_layer0_accuracy: 0.3056 - output_layer0_mean_squared_error: 1.5437 - output_layer1_accuracy: 0.3056 - output_layer1_mean_squared_error: 1.5437 - output_layer2_accuracy: 0.3056 - output_layer2_mean_squared_error: 1.5437 - output_layer3_accuracy: 0.3056 - output_layer3_mean_squared_error: 1.5437 - output_l

...

6/6 [==============================] - ETA: 0s - loss: 32.4167 - output_layer0_loss: 1.5437 - output_layer1_loss: 1.5437 - output_layer2_loss: 1.5437 - output_layer3_loss: 1.5437 - output_layer4_loss: 1.5437 - output_layer5_loss: 1.5437 - output_layer6_loss: 1.5437 - output_layer7_loss: 1.5437 - output_layer8_loss: 1.5437 - output_layer9_loss: 1.5437 - output_layer10_loss: 1.5437 - output_layer11_loss: 1.5437 - output_layer12_loss: 1.5437 - output_layer13_loss: 1.5437 - output_layer14_loss: 1.5437 - output_layer15_loss: 1.5437 - output_layer16_loss: 1.5437 - output_layer17_loss: 1.5437 - output_layer18_loss: 1.5437 - output_layer19_loss: 1.5437 - output_layer20_loss: 1.5437 - output_layer0_accuracy: 0.3056 - output_layer0_mean_squared_error: 1.5437 - output_layer1_accuracy: 0.3056 - output_layer1_mean_squared_error: 1.5437 - output_layer2_accuracy: 0.3056 - output_layer2_mean_squared_error: 1.5437 - output_layer3_accuracy: 0.3056 - output_layer3_mean_squared_error: 1.5437 - output_laye

6/6 [==============================] - ETA: 0s - loss: 32.4167 - output_layer0_loss: 1.5437 - output_layer1_loss: 1.5437 - output_layer2_loss: 1.5437 - output_layer3_loss: 1.5437 - output_layer4_loss: 1.5437 - output_layer5_loss: 1.5437 - output_layer6_loss: 1.5437 - output_layer7_loss: 1.5437 - output_layer8_loss: 1.5437 - output_layer9_loss: 1.5437 - output_layer10_loss: 1.5437 - output_layer11_loss: 1.5437 - output_layer12_loss: 1.5437 - output_layer13_loss: 1.5437 - output_layer14_loss: 1.5437 - output_layer15_loss: 1.5437 - output_layer16_loss: 1.5437 - output_layer17_loss: 1.5437 - output_layer18_loss: 1.5437 - output_layer19_loss: 1.5437 - output_layer20_loss: 1.5437 - output_layer0_accuracy: 0.3056 - output_layer0_mean_squared_error: 1.5437 - output_layer1_accuracy: 0.3056 - output_layer1_mean_squared_error: 1.5437 - output_layer2_accuracy: 0.3056 - output_layer2_mean_squared_error: 1.5437 - output_layer3_accuracy: 0.3056 - output_layer3_mean_squared_error: 1.5437 - output_laye

6/6 [==============================] - ETA: 0s - loss: 32.4167 - output_layer0_loss: 1.5437 - output_layer1_loss: 1.5437 - output_layer2_loss: 1.5437 - output_layer3_loss: 1.5437 - output_layer4_loss: 1.5437 - output_layer5_loss: 1.5437 - output_layer6_loss: 1.5437 - output_layer7_loss: 1.5437 - output_layer8_loss: 1.5437 - output_layer9_loss: 1.5437 - output_layer10_loss: 1.5437 - output_layer11_loss: 1.5437 - output_layer12_loss: 1.5437 - output_layer13_loss: 1.5437 - output_layer14_loss: 1.5437 - output_layer15_loss: 1.5437 - output_layer16_loss: 1.5437 - output_layer17_loss: 1.5437 - output_layer18_loss: 1.5437 - output_layer19_loss: 1.5437 - output_layer20_loss: 1.5437 - output_layer0_accuracy: 0.3056 - output_layer0_mean_squared_error: 1.5437 - output_layer1_accuracy: 0.3056 - output_layer1_mean_squared_error: 1.5437 - output_layer2_accuracy: 0.3056 - output_layer2_mean_squared_error: 1.5437 - output_layer3_accuracy: 0.3056 - output_layer3_mean_squared_error: 1.5437 - output_laye

6/6 [==============================] - ETA: 0s - loss: 32.4167 - output_layer0_loss: 1.5437 - output_layer1_loss: 1.5437 - output_layer2_loss: 1.5437 - output_layer3_loss: 1.5437 - output_layer4_loss: 1.5437 - output_layer5_loss: 1.5437 - output_layer6_loss: 1.5437 - output_layer7_loss: 1.5437 - output_layer8_loss: 1.5437 - output_layer9_loss: 1.5437 - output_layer10_loss: 1.5437 - output_layer11_loss: 1.5437 - output_layer12_loss: 1.5437 - output_layer13_loss: 1.5437 - output_layer14_loss: 1.5437 - output_layer15_loss: 1.5437 - output_layer16_loss: 1.5437 - output_layer17_loss: 1.5437 - output_layer18_loss: 1.5437 - output_layer19_loss: 1.5437 - output_layer20_loss: 1.5437 - output_layer0_accuracy: 0.3056 - output_layer0_mean_squared_error: 1.5437 - output_layer1_accuracy: 0.3056 - output_layer1_mean_squared_error: 1.5437 - output_layer2_accuracy: 0.3056 - output_layer2_mean_squared_error: 1.5437 - output_layer3_accuracy: 0.3056 - output_layer3_mean_squared_error: 1.5437 - output_laye

INFO:tensorflow:Assets written to: models/bert_t21/assets


In [511]:
subjects_split

{'test': ['subject9798',
  'subject7039',
  'subject436',
  'subject6619',
  'subject4058',
  'subject5897',
  'subject2432',
  'subject9218'],
 'train': ['subject3993',
  'subject6635',
  'subject2903',
  'subject5791',
  'subject9694',
  'subject2341',
  'subject3707',
  'subject1272',
  'subject9454',
  'subject2961',
  'subject2827',
  'subject6900']}

In [ ]:
for d in DataGenerator(user_level_data, set_type='train', 
                                     subjects_split=subjects_split):
    print(d[0])
    break

In [ ]:
tf.test.is_gpu_available()

# SVM

In [1]:
from sklearn.svm import SVC
from sklearn.model_selection import cross_val_score


In [2]:
writings_df = writings_df.fillna(value={'text': '', 'title':''})
column_functions = {'text': lambda t: " ".join(t), 
                                        'title': lambda t: " ".join(t),
                                        'text_len': 'sum',
                                        'title_len': 'sum',
                                        'tokenized_text': 'sum',
                                        'tokenized_title': 'sum'
                     }
column_functions.update({'label%i'%i: 'min' for i in range(21)})
column_functions.update({c: 'mean' for c in list(categories) + emotions + ["pronouns"]})
writings_per_user_df = writings_df.groupby('subject').aggregate(column_functions)

NameError: name 'writings_df' is not defined

In [36]:
writings_per_user_df.head()

text  \
subject                                                          
subject1272   Just waking up every morning and talking to m...   
subject2341   If you need to talk to someone, it's not a ba...   
subject2432   *kid   A dataminer said that the octoling gir...   
subject2827   Im so sorry youve had a negative experience. ...   
subject2903   That was not at all how it was, but not gonna...   

                                                         title  text_len  \
subject                                                                    
subject1272                                                ...    1156.0   
subject2341                                                ...    6911.0   
subject2432                                                ...    7125.0   
subject2827           Opinions on high school anxiety      ...   17010.0   
subject2903                                                ...   15338.0   

             title_len                                     tokenized_text  \
subject                                                                     
subject1272       12.0  [just, waking, up, every, morning, and, talkin...   
subject2341        0.0  [if, you, need, to, talk, to, someone, it, s, ...   
subject2432       63.0  [kid, a, dataminer, said, that, the, octoling,...   
subject2827      130.0  [im, so, sorry, youve, had, a, negative, exper...   
subject2903       12.0  [that, was, not, at, all, how, it, was, but, n...   

                                               tokenized_title  label0  \
subject                                                                  
subject1272  [thank, you, trump, very, cool, facts, finally...       1   
subject2341                                                 []       1   
subject2432  [what, s, the, point, okay, what, based, on, y...       1   
subject2827  [opinions, on, high, school, anxiety, need, ad...       1   
subject2903  [reddit, which, current, bands, artists, are, ...       0   

             label1  label2  label3  ...  anticipation   disgust      fear  \
subject                              ...                                     
subject1272       2       2       1  ...      0.024889  0.030528  0.025334   
subject2341       2       3       2  ...      0.034064  0.009286  0.028078   
subject2432       3       3       2  ...      0.014419  0.011440  0.016223   
subject2827       3       3       2  ...      0.039748  0.012513  0.019591   
subject2903       0       1       1  ...      0.021783  0.008517  0.015851   

                  joy  negative  positive   sadness  surprise     trust  \
subject                                                                   
subject1272  0.025333  0.055499  0.053095  0.019931  0.015196  0.037916   
subject2341  0.031474  0.041094  0.058560  0.029255  0.023046  0.045392   
subject2432  0.016127  0.030910  0.044589  0.016004  0.010126  0.025531   
subject2827  0.043596  0.027667  0.071131  0.023701  0.021699  0.043266   
subject2903  0.023864  0.023307  0.047234  0.012222  0.010885  0.029729   

             pronouns  
subject                
subject1272  0.061013  
subject2341  0.041899  
subject2432  0.036645  
subject2827  0.051753  
subject2903  0.041074  

[5 rows x 101 columns]

### Universal sentence encoder

In [1]:
import tensorflow as tf
import tensorflow_hub as hub
# import sentencepiece
# import tensorflow_text


ImportError: Traceback (most recent call last):
  File "/usr/local/tensorflow/python3.5/1.13.1/lib/python3.5/site-packages/tensorflow/python/pywrap_tensorflow.py", line 58, in <module>
    from tensorflow.python.pywrap_tensorflow_internal import *
  File "/usr/local/tensorflow/python3.5/1.13.1/lib/python3.5/site-packages/tensorflow/python/pywrap_tensorflow_internal.py", line 28, in <module>
    _pywrap_tensorflow_internal = swig_import_helper()
  File "/usr/local/tensorflow/python3.5/1.13.1/lib/python3.5/site-packages/tensorflow/python/pywrap_tensorflow_internal.py", line 24, in swig_import_helper
    _mod = imp.load_module('_pywrap_tensorflow_internal', fp, pathname, description)
  File "/home/anasab/tfvenv/lib/python3.5/imp.py", line 242, in load_module
    return load_dynamic(name, filename, file)
  File "/home/anasab/tfvenv/lib/python3.5/imp.py", line 342, in load_dynamic
    return _load(spec)
ImportError: libcublas.so.10.0: cannot open shared object file: No such file or director

In [ ]:
import tensorflow as tf
import tensorflow_hub as hub
module_url = "https://tfhub.dev/google/universal-sentence-encoder-large/3"
# Import the Universal Sentence Encoder's TF Hub module
embed = hub.Module(module_url)

In [3]:
embed_layer = hub.KerasLayer("https://tfhub.dev/google/universal-sentence-encoder-large/4",input_shape=[],dtype=tf.string,trainable=True)

model = tf.keras.Sequential()
model.add(embed_layer)
model.add(tf.keras.layers.Dense(16, activation='relu'))
model.add(tf.keras.layers.Dense(1, activation='sigmoid'))

model.summary()

model.compile(optimizer='adam',
          loss='binary_crossentropy',
          metrics=['accuracy'])

history = model.fit(train_dataset,
                validation_data=validation_dataset,
                epochs=30,
                verbose=1
               )

InvalidArgumentError: assertion failed: [0] [Op:Assert] name: EagerVariableNameReuse

In [17]:
tf.version

<module 'tensorflow_core._api.v2.version' from '/home/anasab/tfvenv/lib/python3.5/site-packages/tensorflow_core/_api/v2/version/__init__.py'>

In [6]:
g = tf.Graph()
with g.as_default():
    use = hub.load("https://tfhub.dev/google/universal-sentence-encoder/4")
    # use = tf.saved_model.load("https://tfhub.dev/google/universal-sentence-encoder-multilingual/3")
    # hub.Module("https://tfhub.dev/google/universal-sentence-encoder-multilingual-large/3")

W0328 14:03:56.196056 139845059770112 deprecation.py:506] From /home/anasab/tfvenv/lib/python3.5/site-packages/tensorflow_core/python/ops/resource_variable_ops.py:1786: calling BaseResourceVariable.__init__ (from tensorflow.python.ops.resource_variable_ops) with constraint is deprecated and will be removed in a future version.
Instructions for updating:
If using Keras pass *_constraint arguments to layers.


In [4]:
tf.compat.v1.disable_eager_execution()

module_url = "https://tfhub.dev/google/universal-sentence-encoder/4" #@param ["https://tfhub.dev/google/universal-sentence-encoder/4", "https://tfhub.dev/google/universal-sentence-encoder-large/5"]
model = hub.load(module_url)

Instructions for updating:
If using Keras pass *_constraint arguments to layers.


Instructions for updating:
If using Keras pass *_constraint arguments to layers.


In [5]:
with tf.compat.v1.Session() as session:
    session.run([tf.compat.v1.global_variables_initializer(), tf.compat.v1.tables_initializer()])
    message_embeddings = session.run(embed(messages))

InternalError: Dst tensor is not initialized.
	 [[node RestoreV2 (defined at /home/anasab/tftf3.6/local/lib/python3.6/site-packages/tensorflow_hub/module_v2.py:95) ]]

Original stack trace for 'RestoreV2':
  File "/usr/lib/python3.6/runpy.py", line 193, in _run_module_as_main
    "__main__", mod_spec)
  File "/usr/lib/python3.6/runpy.py", line 85, in _run_code
    exec(code, run_globals)
  File "/home/anasab/tftf3.6/local/lib/python3.6/site-packages/ipykernel_launcher.py", line 16, in <module>
    app.launch_new_instance()
  File "/home/anasab/tftf3.6/local/lib/python3.6/site-packages/traitlets/config/application.py", line 664, in launch_instance
    app.start()
  File "/home/anasab/tftf3.6/local/lib/python3.6/site-packages/ipykernel/kernelapp.py", line 583, in start
    self.io_loop.start()
  File "/home/anasab/tftf3.6/local/lib/python3.6/site-packages/tornado/platform/asyncio.py", line 149, in start
    self.asyncio_loop.run_forever()
  File "/usr/lib/python3.6/asyncio/base_events.py

In [ ]:
message_embeddings

In [14]:
embed = hub.Module("../resources/sentence_wise_email/module/module_useT")

RuntimeError: variable_scope module_2/ was unused but the corresponding name_scope was already taken.

In [12]:
with tf.compat.v1.Session() as sess:
    model(["The cat is on the mat"])

AssertionError: 

In [58]:
# features = [np.random.rand(75) for i in range(20)]
features = writings_per_user_df[list(categories) + emotions + ["pronouns"]]

def cross_validation(folds=2):
    svmmodels= {}
    total_score = 0
    for l in range(21):
#         print("Classifier for label", l)
        labels = writings_per_user_df['label%d' % l].values
        svmmodels[l] = SVC(kernel='rbf', C=5)
        cvscores = cross_val_score(svmmodels[l], features, labels, cv=folds)
#         print(sum(cvscores)/folds, cvscores)
        total_score += sum(cvscores)/folds
    return total_score/21

print(cross_validation())

0.44047619047619047


/home/anasab/tftf3.6/local/lib/python3.6/site-packages/sklearn/model_selection/_split.py:667: UserWarning: The least populated class in y has only 1 members, which is less than n_splits=2.
  % (min_groups, self.n_splits)), UserWarning)
/home/anasab/tftf3.6/local/lib/python3.6/site-packages/sklearn/model_selection/_split.py:667: UserWarning: The least populated class in y has only 1 members, which is less than n_splits=2.
  % (min_groups, self.n_splits)), UserWarning)
/home/anasab/tftf3.6/local/lib/python3.6/site-packages/sklearn/model_selection/_split.py:667: UserWarning: The least populated class in y has only 1 members, which is less than n_splits=2.
  % (min_groups, self.n_splits)), UserWarning)
/home/anasab/tftf3.6/local/lib/python3.6/site-packages/sklearn/model_selection/_split.py:667: UserWarning: The least populated class in y has only 1 members, which is less than n_splits=2.
  % (min_groups, self.n_splits)), UserWarning)
/home/anasab/tftf3.6/local/lib/python3.6/site-packages/s

In [425]:
def results_for_label(features, l, train_examples=5):
    labels = writings_per_user_df['label%d' % l].values
    svmmodel=SVC()
    svmmodel.fit(features[:train_examples], labels[:train_examples])
    predictions = svmmodel.predict(features[train_examples:])
    print(l, predictions, labels[train_examples:], labels[:train_examples])
    return labels[train_examples:]==predictions

In [426]:
features

funct   article    affect    negemo       sad   cogmech  \
subject                                                                   
subject1272  0.590753  0.042808  0.078767  0.036815  0.004281  0.189212   
subject2341  0.606280  0.038489  0.087976  0.035595  0.007524  0.216032   
subject2432  0.536311  0.067613  0.053005  0.020033  0.002365  0.164997   
subject2827  0.612485  0.038448  0.106301  0.034597  0.010385  0.205893   
subject2903  0.597980  0.058176  0.055244  0.019023  0.003388  0.189186   
subject2961  0.611006  0.038209  0.084884  0.034421  0.008577  0.212320   
subject3707  0.472825  0.040254  0.056373  0.026718  0.006370  0.158801   
subject3993  0.509612  0.062823  0.047135  0.014031  0.002421  0.161933   
subject4058  0.569715  0.084511  0.057204  0.028526  0.003428  0.172183   
subject436   0.565337  0.055708  0.067400  0.035763  0.000688  0.191884   
subject5791  0.573240  0.058490  0.070405  0.029054  0.005607  0.187831   
subject5897  0.549936  0.060866  0.047150  0.012002  0.003000  0.186884   
subject6619  0.495265  0.054668  0.049106  0.015183  0.003508  0.155334   
subject6635  0.584304  0.052760  0.062810  0.022110  0.002932  0.192684   
subject6900  0.580217  0.056568  0.061016  0.025872  0.004009  0.182798   
subject7039  0.545579  0.067460  0.052769  0.018200  0.003479  0.158058   
subject9218  0.577348  0.050986  0.071207  0.038953  0.006327  0.207418   
subject9454  0.602289  0.047210  0.070458  0.035050  0.005007  0.177396   
subject9694  0.502722  0.069464  0.054293  0.017566  0.002831  0.148654   
subject9798  0.535561  0.059967  0.047818  0.019384  0.002710  0.174528   

                inhib       bio      body   achieve  ...  anticipation  \
subject                                              ...                 
subject1272  0.001712  0.035959  0.015411  0.013699  ...      0.024889   
subject2341  0.003907  0.013312  0.003762  0.017364  ...      0.034064   
subject2432  0.005147  0.013495  0.005287  0.017947  ...      0.014419   
subject2827  0.007001  0.021587  0.004201  0.025088  ...      0.039748   
subject2903  0.003453  0.026254  0.008990  0.013876  ...      0.021783   
subject2961  0.004456  0.035869  0.008355  0.022502  ...      0.027696   
subject3707  0.005783  0.032637  0.004418  0.017728  ...      0.033694   
subject3993  0.005494  0.018872  0.004479  0.018782  ...      0.026700   
subject4058  0.006208  0.008912  0.002323  0.017557  ...      0.025554   
subject436   0.004127  0.028886  0.001376  0.013067  ...      0.028608   
subject5791  0.004460  0.015737  0.007391  0.019688  ...      0.030570   
subject5897  0.006858  0.029147  0.009001  0.017574  ...      0.023568   
subject6619  0.005261  0.006815  0.002155  0.028211  ...      0.033144   
subject6635  0.005319  0.024587  0.010805  0.017924  ...      0.024185   
subject6900  0.005012  0.030696  0.011965  0.015411  ...      0.032718   
subject7039  0.004193  0.017051  0.005870  0.016088  ...      0.022515   
subject9218  0.003846  0.030021  0.008808  0.013646  ...      0.024682   
subject9454  0.005365  0.021102  0.007511  0.010014  ...      0.061261   
subject9694  0.005879  0.022356  0.009363  0.015170  ...      0.034708   
subject9798  0.004429  0.013745  0.003993  0.016141  ...      0.021804   

              disgust      fear       joy  negative  positive   sadness  \
subject                                                                   
subject1272  0.030528  0.025334  0.025333  0.055499  0.053095  0.019931   
subject2341  0.009286  0.028078  0.031474  0.041094  0.058560  0.029255   
subject2432  0.011440  0.016223  0.016127  0.030910  0.044589  0.016004   
subject2827  0.012513  0.019591  0.043596  0.027667  0.071131  0.023701   
subject2903  0.008517  0.015851  0.023864  0.023307  0.047234  0.012222   
subject2961  0.013048  0.017931  0.022866  0.028927  0.044044  0.019895   
subject3707  0.006842  0.027104  0.018208  0.036167  0.042436  0.017377   
subject3993  0.008983  0.015668  0.022874  0.031980  0.056786

In [427]:
cumresults = []
for l in range(21):
    results = results_for_label(features, l)
    cumresults.append(results)

nrusers = len(cumresults[0])
nrques = 21
correct_per_user = {u: 0 for u in range(nrusers)}
for q, ques in enumerate(cumresults):
    for u, answ in enumerate(cumresults[q]):
        if answ:
            correct_per_user[u] += 1

for u in correct_per_user:
    print("u", u, correct_per_user[u]/nrques)
print("AHR", sum(correct_per_user.values())/nrusers/nrques)

0 [1 1 1 1 1 1 1 1 1 1 1 1 1 1 1] [1 1 0 0 2 1 2 0 0 1 1 2 1 0 1] [1 1 1 1 0]
1 [2 3 3 3 3 3 3 3 2 3 3 2 2 3 3] [1 3 0 0 1 0 3 0 1 1 1 2 3 0 1] [2 2 3 3 0]
2 [3 3 3 3 3 3 3 3 3 3 3 3 3 3 3] [1 0 0 0 2 1 3 0 1 2 0 1 3 2 2] [2 3 3 3 1]
3 [2 2 2 2 2 2 2 2 2 2 2 2 2 2 2] [1 1 0 1 3 1 2 1 1 1 1 2 2 0 1] [1 2 2 2 1]
4 [3 3 3 3 3 3 3 3 3 3 3 3 3 3 3] [0 0 0 0 2 0 1 0 1 0 0 1 1 1 3] [0 3 3 3 0]
5 [2 2 2 2 2 2 2 2 2 2 2 2 2 2 2] [0 0 0 0 0 0 0 0 0 0 0 0 3 0 0] [1 2 2 2 0]
6 [3 2 2 2 2 2 2 2 3 2 2 3 3 2 2] [1 0 0 0 3 2 2 0 3 1 2 3 3 0 1] [3 3 2 2 1]
7 [3 2 2 2 2 2 2 2 2 2 2 3 3 2 2] [1 1 0 0 3 1 2 0 1 1 0 2 3 0 1] [2 3 2 3 0]
8 [1 2 2 2 2 2 2 2 1 2 2 1 1 2 2] [1 1 0 1 1 0 1 0 1 1 0 1 2 0 0] [1 1 2 2 0]
9 [0 0 0 0 0 0 0 0 0 0 0 0 0 0 0] [1 2 0 0 2 0 0 0 0 1 0 2 3 0 0] [3 0 1 2 0]
10 [0 1 1 1 1 1 1 1 0 0 1 0 1 1 1] [1 3 0 0 1 0 0 0 2 1 0 2 2 1 2] [3 0 1 1 0]
11 [1 1 1 1 1 1 1 1 1 1 1 1 1 1 1] [1 0 0 0 3 1 3 1 1 1 1 3 3 0 3] [1 2 3 1 0]
12 [2 2 2 2 2 2 2 2 2 2 2 2 2 2 2] [1 0 0 0 2 0 2 0 3 0 0 1 3 

# Extra analysis


### Extract LIWC

In [409]:
def merge_tokens(row):
    tokens = []
    if row.tokenized_text:
        tokens += row.tokenized_text
    if row.tokenized_title:
        tokens += row.tokenized_title
    return tokens
writings_df['all_tokens'] = writings_df.apply (lambda row: merge_tokens(row), axis=1)

In [ ]:
# TODO: include the title
def extract_emotions(tokens, emotion, relative=True):
    if not tokens:
        return None
    emotion_words = [t for t in tokens 
                     if t in nrc_lexicon[emotion]]
    if relative:
        return len(emotion_words) / len(tokens)
    else:
        return len(emotion_words)
    
    return encoded_emotions

from functools import partial
for emotion in emotions:
    writings_df[emotion] = writings_df['all_tokens'].apply(partial(extract_emotions, emotion=emotion, 
                                                                   relative=True))

In [ ]:
writings_df['pronouns'] = writings_df['all_tokens'].apply(partial(encode_pronouns, relative=True))

In [ ]:
writings_df[['label%i'%i for i in range(21)] + ['text', 'pronouns', 'text_len'] + emotions].corr('spearman')

In [ ]:
# writings_df['label15'] = writings_df['label15'].apply(lambda l: encode_labels([l])[0])

In [ ]:
# writings_df['label17'] = writings_df['label17'].apply(lambda l: encode_labels([l])[0])

In [ ]:
writings_df.groupby('subject').mean()[
    ['label%i'%i for i in range(21)] + ['pronouns', 'text_len'] + emotions].corr(
    'spearman')[['pronouns', 'text_len'] + emotions]

In [ ]:
writings_df.corrwith?

In [405]:
from liwc_readDict import readDict

liwc = readDict('/home/anasab/resources/liwc.dic')
categories = [c for (w,c) in liwc]
set(categories)
liwc_dict = {}
for (w, c) in liwc:
    if c not in liwc_dict:
        liwc_dict[c] = []
    liwc_dict[c].append(w)

In [413]:
writings_per_user_df['all_tokens'] = writings_per_user_df.apply (lambda row: merge_tokens(row), axis=1)

In [414]:
def encode_liwc_categories(tokens, category_words, relative=True):
    category_cnt = 0
    if not tokens:
        return None
    text_len = len(tokens)
    for t in tokens:
        for word in category_words:
            if t==word or (word[-1]=='*' and t.startswith(word[:-1])) \
            or (t==word.split("'")[0]):
                category_cnt += 1
                break # one token cannot belong to more than one word in the category
    if relative:
        return category_cnt/text_len
    else:
        return category_cnt

In [415]:
%%time
from functools import partial
# for categ in ['negemo', 'posemo', 'affect', 'sad', 'anx', 'pronoun']:#liwc_dict.keys():
for categ in liwc_dict.keys():
#     if categ in writings_df.columns:
#         continue
    print("Encoding for category %s..." % categ)
    writings_per_user_df[categ] = writings_per_user_df['all_tokens'].apply(partial(encode_liwc_categories, 
                                                                   category_words=liwc_dict[categ], 
                                                                   relative=True))


Encoding for category funct...
Encoding for category article...
Encoding for category affect...
Encoding for category negemo...
Encoding for category sad...
Encoding for category cogmech...
Encoding for category inhib...
Encoding for category bio...
Encoding for category body...
Encoding for category achieve...
Encoding for category health...
Encoding for category sexual...
Encoding for category adverb...
Encoding for category preps...
Encoding for category space...
Encoding for category relativ...
Encoding for category time...
Encoding for category work...
Encoding for category certain...
Encoding for category assent...
Encoding for category anger...
Encoding for category posemo...
Encoding for category insight...
Encoding for category verb...
Encoding for category past...
Encoding for category money...
Encoding for category percept...
Encoding for category social...
Encoding for category friend...
Encoding for category motion...
Encoding for category cause...
Encoding for category le

In [ ]:
relevant_categs = ['posemo', 'negemo', 'anx', 'sad', 'affect', 'feel', 'social', 'health', 
                   'sexual', 'present', 'cogmech', 'inhib']
writings_df.groupby('subject').mean()[
    ['label%i'%i for i in range(21)] + relevant_categs].corr(
    'spearman')[relevant_categs]

In [ ]:
list(writings_df.groupby('subject').min()[
    ['label%i'%i for i in range(21)] + list(liwc_dict.keys())].corr()[list(liwc_dict.keys())].mean().sort_values().index)

In [ ]:
pickle.dump(writings_df, open('writings_df_T2_liwc.pkl', 'wb+'))